# About
Notebook containing the following simulations using the Monte Carlo method:
- [Estimating $\pi$](#Estimating-$\pi$)

In [1]:
import time
import numpy as np
from typing import Tuple, List
from bokeh.plotting import figure, ColumnDataSource
from bokeh.io import output_notebook, show, push_notebook
from bokeh.models import Label
from tqdm.notebook import tqdm
from matplotlib import pyplot as plt, animation, rc, patches, colors

In [2]:
rng = np.random.default_rng(1)

# Estimating $\pi$
Estimating $\pi$ by generating random positions and calculating the proportion that lie within the quadrant of a circle.

This method of estimating $\pi$ is the following:
- Draw a circle quadrant inside a square;
- Calculate the ratio between the area of the circle and square;
- Randomly generate positions and count whether they're inside or outside the circle; and
- The ratio of the positions is an estimation of the ratio of the areas.

In [3]:
output_notebook()

Loading BokehJS ...

## Calculating Areas
The figure below shows the setup of the circle quadrant inside the square. The area ratio ($R$) calculations are shown below where $A_{c}$ and $A_{s}$ are the areas of the square and circle quadrant, respectively, and $r$ is the radius of the circle and length of the square.
$$
A_{c} = \frac{\pi r^2}{4}
$$
$$
A_{s} = r^2
$$
$$
R = \frac{A_{c}}{A_{s}} = \frac{\pi r^2}{4 r^2} = \frac{\pi}{4}
$$

In [4]:
p = figure(x_range=(0, 1), y_range=(0, 1), title="Circle Quadrant")
p.min_border = 40
p.rect(.5, .5, 1, 1, color="orange")
p.circle(0, 0, radius=1, alpha=.7)
show(p)

## Generating Positions
Randomly generating the positions on the graph and using the ratio inside the circle quadrant to approximate $\pi$.
$$
\pi \approx 4 \frac{C_c}{C_s}
$$
where $C_c$ is the number of points inside the circle quadrant and $C_s$ is the number of points inside the whole square.

In [5]:
def estimate_pi(inside: int, outside: int) -> float:
    return 4 * inside / (inside + outside)

def generate_points(n: int, radius: int) -> Tuple[np.ndarray, np.ndarray, List[int]]:
    xy = rng.random((2, n))
    cond = np.sum(xy ** 2, axis=0) <= radius
    colour = np.where(cond, "green", "red")
    inside = np.sum(cond)
    outside = np.sum(cond == 0)
    return xy, colour, [inside, outside]

## Plotting with Bokeh
Generating positions and plotting live with bokeh.

In [6]:
RADIUS = 1
MAX_STEP = 10000
STEP_SIZE = 100
DELTA_T = 0.01
p = figure(x_range=(0, RADIUS), y_range=(0, RADIUS), title="Estimating \u03C0")
p.min_border = 40
p.circle(0, 0, radius=RADIUS, color="gray", alpha=.5)
source = ColumnDataSource({"x": [], "y": [], "color": []})
p.scatter("x", "y", source=source, color="color")
label_text = "\u03C0 \u2248 {:.5f} after {} steps"
label = Label(x=0.5, y=0.95, text="\u03C0 \u2248 ?? after 0 steps",
              background_fill_color='white', background_fill_alpha=.8)
p.add_layout(label)

handle = show(p, notebook_handle=True)

count_inside = 0
count_outside = 0
step = 0
pbar = tqdm(total=MAX_STEP, desc="Generating points", dynamic_ncols=True)
while step < MAX_STEP:
    xy, colours, counts = generate_points(STEP_SIZE, RADIUS)
    count_inside += counts[0]
    count_outside += counts[1]
    source.stream({"x": xy[0], "y": xy[1], "color": colours})
    step += STEP_SIZE
    pbar.update(STEP_SIZE)
    # Calculate pi
    pi = estimate_pi(count_inside, count_outside)
    label.text = label_text.format(pi, step)
    push_notebook(handle=handle)
    time.sleep(DELTA_T)
pbar.close()

## Plotting with Matplotlib
Generating positions and creating animation with matplotlib which can then be played after.

In [7]:
fig, ax = plt.subplots(figsize=(10, 10))
fig.tight_layout()
ax.set_title("Estimating $\pi$", fontdict=dict(fontsize="xx-large"))
ax.set_aspect("equal")
ax.set_xlim((0, RADIUS))
ax.set_ylim((0, RADIUS))
circle = patches.Circle((0, 0), radius=RADIUS, color="gray", alpha=.5, zorder=0)
ax.add_patch(circle)
label = ax.annotate(r"$\pi \approx$ ?? after 0 steps", (0.6, 0.96),
                    fontsize="x-large", backgroundcolor=(1, 1, 1, .8))
data = np.array([[], []], dtype=float)
c = np.array([], dtype=float)
# Create initial plot with custom red/green colormap
cmap = colors.ListedColormap(["red", "green"])
norm = colors.BoundaryNorm([0, .5, 1], cmap.N)
scat = ax.scatter(data[0], data[1], c=c, cmap=cmap, norm=norm, s=2)

total_counts = [0, 0]
MAX_STEPS = int(1e5)
step_size = int(np.ceil(np.sqrt(MAX_STEPS)))
count = 0
frames = range(step_size, MAX_STEPS + step_size, step_size)
pbar = tqdm(total=max(frames), desc="Generating animation", dynamic_ncols=True)

def init_fig():
    return (scat,)

def update(step: int):
    global data, c
    xy, colours, counts = generate_points(step_size, RADIUS)
    colours = np.where(colours == "red", 0, 1)
    for i in (0, 1):
        total_counts[i] += counts[i]
    pi = estimate_pi(*total_counts)
    label.set_text(fr"$\pi \approx$ {pi:.5f} after {step} steps")
    data = np.hstack((data, xy))
    c = np.hstack((c, colours))
    scat.set_offsets(data.T)
    scat.set_array(c)
    pbar.update(step_size)
    return (scat,)

anim = animation.FuncAnimation(fig, update, init_func=init_fig, frames=frames,
                               interval=100, blit=True, repeat=False)
rc("animation", html="html5")
display(anim)
pbar.close()
plt.close()